In [2]:
import pandas as pd
import numpy as np
import random
from functools import reduce

In [3]:
df = pd.read_csv("info.csv").iloc[:,1:]
df = df.set_index("Your name")

In [4]:
df

First Person   Second person  Third person  Fourth person  \
Your name                                                              
1                   13.0           12.0          78.0            8.0   
2                   61.0           42.0          39.0            3.0   
3                   61.0           39.0           2.0           69.0   
4                   37.0           21.0          14.0           28.0   
5                   43.0            7.0          30.0           41.0   
...                  ...            ...           ...            ...   
90                   NaN            NaN           NaN            NaN   
91                   NaN            NaN           NaN            NaN   
92                   NaN            NaN           NaN            NaN   
93                   NaN            NaN           NaN            NaN   
94                   NaN            NaN           NaN            NaN   

           Fifth person  
Your name                
1                  34.0  
2                  69.0  
3                  44.0  
4                  51.0  
5                  32.0  
...                 ...  
90                  NaN  
91                  NaN  
92                  NaN  
93                  NaN  
94                  NaN  

[94 rows x 5 columns]

In [5]:
class Evaluation:  
    def VerticleHappiness(self, people):
        HappyPeople = []
        for person in people:
            row, col = self.getRowColFromPerson(person)

            choices = self.getChoices(person)

            if row!=self.numRows-1:
                p = self.Chart[row+1][col]
                rank = self.rank(p,choices)

                if rank in range(1,6) and person not in HappyPeople:
                    HappyPeople.append(person)


            if row!=0:
                p = self.Chart[row-1][col]

                rank = self.rank(p,choices)
 
                if rank in range(1,6) and person not in HappyPeople:
                    HappyPeople.append(person)
        print("Number of People with verticle: %s "%HappyPeople)
            
    def rank(self,p,choices):
        if p in choices: return choices.index(p)+1
        return None
    
    def EvaluateHappiness(self):
        
        Done = []
        for Level in range(1,6):
            
            HappyPeople = []
            NoPreferences = []
            UnHappyPeople = []
            
            for row in range(self.numRows):
                for col in range(self.numCols):
                    person = self.Chart[row][col]
                    if person==0: continue
                
                    if self.NaPerson(person): 
                        NoPreferences.append(person)
                        continue

                    choices = self.getChoices(person)
                    
                    if col!=self.numCols-1:
                        p = self.Chart[row][col+1]
                        
                        rank = self.rank(p,choices)
                        if rank == Level and person not in HappyPeople and person not in Done: 
                            HappyPeople.append(person)
                        
                        
                    if col!=0:
                        p = self.Chart[row][col-1]
                        rank = self.rank(p,choices)
                        
                        if rank == Level and person not in HappyPeople and person not in Done:
                            HappyPeople.append(person)
                        
                        
           
            print("Level %s, # of people %s" %(Level, len(HappyPeople)))
            Done += HappyPeople
                            
        print("# of people No Preferences", len(NoPreferences))
        
        print("Not in Top 5:", 94-len(NoPreferences)-len(Done))
        UnHappyPeople = [p for p in range(1,95) if p not in NoPreferences+Done]
        print("Not in Top 5:", UnHappyPeople)
        self.VerticleHappiness(UnHappyPeople)
        
    

In [6]:
class FunctionTools:
    def getRowColFromPerson(self,person):
        for row in range(self.numRows):
                for col in range(self.numCols):
                    p = self.Chart[row][col]
                    
                    if person==p:
                        
                        return row,col
                    
    def idealPairs(self):
        self.firsts = []
        for pair in self.matches:
            if pair["rank1"] in [1,2,None] and pair["rank2"] in [1,2,None]:
                self.firsts.append(pair)
    
    def makeDict(self, person1, rank1, person2, rank2):
        return {"person1":person1,"rank1":rank1,"person2":person2, "rank2":rank2}
    
    def getChoices(self,p):
        return list(self.df.loc[p])
    
    def removePersonFromMatches(self,person):
        return [pair for pair in matches if not (pair["person1"]==person or pair["person2"]==person)]
    
    def removePersonFromPeople(self,p, people):
        return [person for person in people if person != p]
        
                
    def getMatches(self,person):
        return [pair for pair in self.matches if pair["person1"]==person or pair["person2"]==person]
    
    
    def NaPerson(self,person):
        choices = self.getChoices(person)
        return np.isnan(choices).all()         
    
    def getPeople(self,pair):
        return [pair["person1"],pair["person2"]]
    
    def CompositeScore(self, pair):
        rank1 = pair["rank1"]
        rank2 = pair["rank2"]
        totalRank = rank2*2 if rank1 == None else (rank1*2 if rank2==None else rank1+rank2)
        return totalRank
    
    def findOtherPerson(self,pair, person):
        return pair["person1"] if person != pair["person1"] else pair["person2"]
    
    def findMatchPeople(self,matchesLeft,personLeft, matchesAbove, personAbove):
        peopleLeft = [self.findOtherPerson(pair, personLeft) for pair in matchesLeft]
        peopleAbove = [self.findOtherPerson(pair, personAbove) for pair in matchesAbove]
        return list(set(peopleLeft).union(set(peopleAbove)))
    
    def samePeople(self,pair, p1,p2):
        np1, np2 = pair["person1"],pair["person2"]
        if (np1 == p1 and np2==p2) or (np2 == p1 and np1==p2):
            return True
        return False
    
    
    def getMatch(self,p1,p2):
        match = [pair for pair in self.matches if self.samePeople(pair,p1,p2)]
        if len(match)==0:return None
        return match[0]
    
    def scorePair(self, pair):
        rank1 = pair["rank1"]
        rank2 = pair["rank2"]
        totalRank = rank2*2 if rank1 == None else (rank1*2 if rank2==None else rank1+rank2)
        return totalRank
    

In [70]:

class Students(Evaluation, FunctionTools):
    df = pd.read_csv("info.csv").iloc[:,1:]
    df = df.set_index("Your name")
    def __init__(self):
        self.numCols = 10
        self.numRows = 10
        self.matches()
        self.idealPairs()
        self.MatchesForLonelyPeople()
        self.stringPairs = []
        self.people = list(self.df.index)
        
        self.Chart = np.zeros((self.numRows,self.numCols))
        
      
        #self.Chart[0][0] = 40
        #print(self.lowestCompositeScore(0,1))
        self.createString(0,0, self.people)
        #self.EvaluateHappiness()

        
    def matches(self):
        matches = []
        for person,rankings in self.df.iterrows():
                for rank1,rankedPerson in enumerate(rankings):
                    if not pd.isnull(rankedPerson):
                        OtherPersonChoices = self.getChoices(rankedPerson)
                        if person in OtherPersonChoices:
                            if person > rankedPerson: continue #don't want duplicates if they overlap it will be added by first person
                            rank2 = OtherPersonChoices.index(person)
                            matches.append(self.makeDict(person,rank1+1,rankedPerson,rank2))
                        elif np.isnan(OtherPersonChoices).all():
                            matches.append(self.makeDict(person,rank1+1,rankedPerson,None))
        self.matches = matches
    
    def NoMatches(self):
        haveMatch = reduce(lambda a,b: a+b, [self.getPeople(pair) for pair in self.matches])
        return [p for p in range(1,95) if p not in haveMatch and not self.NaPerson(p)]
    
    def MatchesForLonelyPeople(self):
        needMatch = self.NoMatches()
        for person in needMatch:
            rankings = self.getChoices(person)
            for rank1,rankedPerson in enumerate(rankings):
                if not pd.isnull(rankedPerson):
                    self.matches.append(self.makeDict(person,rank1+1,rankedPerson,rank1+1))
                    
    def CompositeScore(self,person,personLeft, personAbove):
        if len(self.getMatches(person))==1: return -100
        matchLeft = self.getMatch(person,personLeft)
        matchAbove = self.getMatch(person,personAbove)
        
        if matchAbove == None:
            totalRankLeft = self.scorePair(matchLeft)
            return totalRankLeft
        if matchLeft == None:
            totalRankAbove = self.scorePair(matchAbove)
            return 100+totalRankAbove
        
        totalRankLeft = self.scorePair(matchLeft)
        totalRankAbove = 12-self.scorePair(matchAbove)
        return totalRankLeft-.5*(totalRankAbove)
        
    def lowestCompositeScore(self, row,col, people):
        
        personLeft = 0 if col==0 else self.Chart[row][col-1]
        personAbove = 0 if row==0 else self.Chart[row-1][col]
        if (personLeft==0 and personAbove==0): return None
        matchesLeft = self.getMatches(personLeft)
        matchesAbove = self.getMatches(personAbove)
 
        
        peopleOptions = self.findMatchPeople(matchesLeft,personLeft,matchesAbove, personAbove)
        peopleOptions = [person for person in peopleOptions if person in people]
        if len(peopleOptions)==0: return None
        scores = [self.CompositeScore(person, personLeft, personAbove) for person in peopleOptions]
        minScore = min(scores)
        bestPerson = peopleOptions[scores.index(minScore)]
        return bestPerson
        
    
    
    def newPosition(self,row,col):
        if col==self.numCols-1: 
            col =0
            row += 1
        else: col+=1
        return row,col
    
    def createString(self, row, col, people):
        if row == self.numRows: return
        newPerson = self.lowestCompositeScore(row, col, people)
        nrow,ncol = self.newPosition(row,col)
        if newPerson==None:
            if len(people)==0:
                print(self.Chart)
                return
            
            if col==self.numCols-1:
                row,col = self.newPosition(row,col)
                self.createString(nrow, ncol, people)
                
            else: 
                
                for x in people:
                    newPerson = x
                    self.Chart[row][col] = newPerson
                    newpeople = self.removePersonFromPeople(newPerson, people)
                    self.createString(nrow, ncol, newpeople)
                

        else:  
        
            self.Chart[row][col] = newPerson
            newpeople = self.removePersonFromPeople(newPerson, people)

            self.createString(nrow, ncol, newpeople)
    
   
    
    
    

In [ ]:
obj = Students()

[[ 1. 13. 12. 11. 69. 42.  7. 43.  5.  0.]
 [78. 74.  8. 27. 86. 31. 36. 46. 82. 32.]
 [49.  9.  2. 61.  3. 39.  4. 37. 21. 38.]
 [16. 45. 17. 48. 26. 47. 28. 51.  6. 23.]
 [10. 84. 75. 52. 76. 18. 14. 58. 81.  0.]
 [29. 87. 65. 88. 66. 92. 15. 34. 33. 67.]
 [19. 25. 40. 57. 60. 20. 83. 59. 72. 53.]
 [22. 85. 24. 63. 30. 41. 35. 93. 44. 64.]
 [50. 73. 54. 56. 77. 55. 62. 94. 68. 79.]
 [70. 89. 80. 71. 90. 91.  0.  0.  0.  0.]]
[[ 1. 13. 12. 11. 69. 42.  7. 43.  5.  0.]
 [78. 74.  8. 27. 86. 31. 36. 46. 82. 32.]
 [49.  9.  2. 61.  3. 39.  4. 37. 21. 38.]
 [16. 45. 17. 48. 26. 47. 28. 51.  6. 23.]
 [10. 84. 75. 52. 76. 18. 14. 58. 81.  0.]
 [29. 87. 65. 88. 66. 92. 15. 34. 33. 67.]
 [19. 25. 40. 57. 60. 20. 83. 59. 72. 53.]
 [22. 85. 24. 63. 30. 41. 35. 93. 44. 64.]
 [50. 73. 54. 56. 77. 55. 62. 94. 68. 79.]
 [70. 89. 80. 71. 91. 90.  0.  0.  0.  0.]]
[[ 1. 13. 12. 11. 69. 42.  7. 43.  5.  0.]
 [78. 74.  8. 27. 86. 31. 36. 46. 82. 32.]
 [49.  9.  2. 61.  3. 39.  4. 37. 21. 38.]
 [16. 45.

 [91. 80. 68. 70. 89. 90.  0.  0.  0.  0.]]
[[ 1. 13. 12. 11. 69. 42.  7. 43.  5.  0.]
 [78. 74.  8. 27. 86. 31. 36. 46. 82. 32.]
 [49.  9.  2. 61.  3. 39.  4. 37. 21. 38.]
 [16. 45. 17. 48. 26. 47. 28. 51.  6. 23.]
 [10. 84. 75. 52. 76. 18. 14. 58. 81.  0.]
 [29. 87. 65. 88. 66. 92. 15. 34. 33. 67.]
 [19. 25. 40. 57. 60. 20. 83. 59. 72. 53.]
 [22. 85. 24. 63. 30. 41. 35. 93. 44. 64.]
 [50. 73. 54. 56. 77. 55. 62. 94. 71. 79.]
 [91. 80. 68. 89. 70. 90.  0.  0.  0.  0.]]
[[ 1. 13. 12. 11. 69. 42.  7. 43.  5.  0.]
 [78. 74.  8. 27. 86. 31. 36. 46. 82. 32.]
 [49.  9.  2. 61.  3. 39.  4. 37. 21. 38.]
 [16. 45. 17. 48. 26. 47. 28. 51.  6. 23.]
 [10. 84. 75. 52. 76. 18. 14. 58. 81.  0.]
 [29. 87. 65. 88. 66. 92. 15. 34. 33. 67.]
 [19. 25. 40. 57. 60. 20. 83. 59. 72. 53.]
 [22. 85. 24. 63. 30. 41. 35. 93. 44. 64.]
 [50. 73. 54. 56. 77. 55. 62. 94. 71. 79.]
 [91. 80. 68. 90. 70. 89.  0.  0.  0.  0.]]
[[ 1. 13. 12. 11. 69. 42.  7. 43.  5.  0.]
 [78. 74.  8. 27. 86. 31. 36. 46. 82. 32.]
 [49.  9

 [71. 79. 90. 68. 80. 91.  0.  0.  0.  0.]]
[[ 1. 13. 12. 11. 69. 42.  7. 43.  5.  0.]
 [78. 74.  8. 27. 86. 31. 36. 46. 82. 32.]
 [49.  9.  2. 61.  3. 39.  4. 37. 21. 38.]
 [16. 45. 17. 48. 26. 47. 28. 51.  6. 23.]
 [10. 84. 75. 52. 76. 18. 14. 58. 81.  0.]
 [29. 87. 65. 88. 66. 92. 15. 34. 33. 67.]
 [19. 25. 40. 57. 60. 20. 83. 59. 72. 53.]
 [22. 85. 24. 63. 30. 41. 35. 93. 44. 64.]
 [50. 73. 54. 56. 77. 55. 62. 94. 89. 70.]
 [71. 79. 90. 80. 68. 91.  0.  0.  0.  0.]]
[[ 1. 13. 12. 11. 69. 42.  7. 43.  5.  0.]
 [78. 74.  8. 27. 86. 31. 36. 46. 82. 32.]
 [49.  9.  2. 61.  3. 39.  4. 37. 21. 38.]
 [16. 45. 17. 48. 26. 47. 28. 51.  6. 23.]
 [10. 84. 75. 52. 76. 18. 14. 58. 81.  0.]
 [29. 87. 65. 88. 66. 92. 15. 34. 33. 67.]
 [19. 25. 40. 57. 60. 20. 83. 59. 72. 53.]
 [22. 85. 24. 63. 30. 41. 35. 93. 44. 64.]
 [50. 73. 54. 56. 77. 55. 62. 94. 89. 70.]
 [71. 79. 90. 91. 68. 80.  0.  0.  0.  0.]]
[[ 1. 13. 12. 11. 69. 42.  7. 43.  5.  0.]
 [78. 74.  8. 27. 86. 31. 36. 46. 82. 32.]
 [49.  9

 [71. 80. 94. 62. 70. 89. 91.  0.  0.  0.]]
[[ 1. 13. 12. 11. 69. 42.  7. 43.  5.  0.]
 [78. 74.  8. 27. 86. 31. 36. 46. 82. 32.]
 [49.  9.  2. 61.  3. 39.  4. 37. 21. 38.]
 [16. 45. 17. 48. 26. 47. 28. 51.  6. 23.]
 [10. 84. 75. 52. 76. 18. 14. 58. 81.  0.]
 [29. 87. 65. 88. 66. 92. 15. 34. 33. 67.]
 [19. 25. 40. 57. 60. 20. 83. 59. 72. 53.]
 [22. 85. 24. 63. 30. 41. 35. 93. 44. 64.]
 [50. 73. 54. 56. 77. 55. 68. 79. 90. 79.]
 [71. 80. 94. 62. 89. 70. 91.  0.  0.  0.]]
[[ 1. 13. 12. 11. 69. 42.  7. 43.  5.  0.]
 [78. 74.  8. 27. 86. 31. 36. 46. 82. 32.]
 [49.  9.  2. 61.  3. 39.  4. 37. 21. 38.]
 [16. 45. 17. 48. 26. 47. 28. 51.  6. 23.]
 [10. 84. 75. 52. 76. 18. 14. 58. 81.  0.]
 [29. 87. 65. 88. 66. 92. 15. 34. 33. 67.]
 [19. 25. 40. 57. 60. 20. 83. 59. 72. 53.]
 [22. 85. 24. 63. 30. 41. 35. 93. 44. 64.]
 [50. 73. 54. 56. 77. 55. 68. 79. 90. 79.]
 [71. 80. 94. 62. 91. 70. 89.  0.  0.  0.]]
[[ 1. 13. 12. 11. 69. 42.  7. 43.  5.  0.]
 [78. 74.  8. 27. 86. 31. 36. 46. 82. 32.]
 [49.  9

 [71. 79. 90. 80. 68. 91. 70.  0.  0.  0.]]
[[ 1. 13. 12. 11. 69. 42.  7. 43.  5.  0.]
 [78. 74.  8. 27. 86. 31. 36. 46. 82. 32.]
 [49.  9.  2. 61.  3. 39.  4. 37. 21. 38.]
 [16. 45. 17. 48. 26. 47. 28. 51.  6. 23.]
 [10. 84. 75. 52. 76. 18. 14. 58. 81.  0.]
 [29. 87. 65. 88. 66. 92. 15. 34. 33. 67.]
 [19. 25. 40. 57. 60. 20. 83. 59. 72. 53.]
 [22. 85. 24. 63. 30. 41. 35. 93. 44. 64.]
 [50. 73. 54. 56. 77. 55. 70. 89. 62. 94.]
 [71. 79. 90. 91. 68. 80. 70.  0.  0.  0.]]
[[ 1. 13. 12. 11. 69. 42.  7. 43.  5.  0.]
 [78. 74.  8. 27. 86. 31. 36. 46. 82. 32.]
 [49.  9.  2. 61.  3. 39.  4. 37. 21. 38.]
 [16. 45. 17. 48. 26. 47. 28. 51.  6. 23.]
 [10. 84. 75. 52. 76. 18. 14. 58. 81.  0.]
 [29. 87. 65. 88. 66. 92. 15. 34. 33. 67.]
 [19. 25. 40. 57. 60. 20. 83. 59. 72. 53.]
 [22. 85. 24. 63. 30. 41. 35. 93. 44. 64.]
 [50. 73. 54. 56. 77. 55. 70. 89. 62. 94.]
 [71. 79. 90. 91. 80. 68. 70.  0.  0.  0.]]
[[ 1. 13. 12. 11. 69. 42.  7. 43.  5.  0.]
 [78. 74.  8. 27. 86. 31. 36. 46. 82. 32.]
 [49.  9

...

 [71. 79. 90. 68. 80. 91. 55.  0.  0.  0.]]
[[ 1. 13. 12. 11. 69. 42.  7. 43.  5.  0.]
 [78. 74.  8. 27. 86. 31. 36. 46. 82. 32.]
 [49.  9.  2. 61.  3. 39.  4. 37. 21. 38.]
 [16. 45. 17. 48. 26. 47. 28. 51.  6. 23.]
 [10. 84. 75. 52. 76. 18. 14. 58. 81.  0.]
 [29. 87. 65. 88. 66. 92. 15. 34. 33. 67.]
 [19. 25. 40. 57. 60. 20. 83. 59. 72. 53.]
 [22. 85. 24. 63. 30. 41. 35. 93. 44. 64.]
 [50. 73. 54. 56. 77. 89. 70. 55. 62. 94.]
 [71. 79. 90. 80. 68. 91. 55.  0.  0.  0.]]
[[ 1. 13. 12. 11. 69. 42.  7. 43.  5.  0.]
 [78. 74.  8. 27. 86. 31. 36. 46. 82. 32.]
 [49.  9.  2. 61.  3. 39.  4. 37. 21. 38.]
 [16. 45. 17. 48. 26. 47. 28. 51.  6. 23.]
 [10. 84. 75. 52. 76. 18. 14. 58. 81.  0.]
 [29. 87. 65. 88. 66. 92. 15. 34. 33. 67.]
 [19. 25. 40. 57. 60. 20. 83. 59. 72. 53.]
 [22. 85. 24. 63. 30. 41. 35. 93. 44. 64.]
 [50. 73. 54. 56. 77. 89. 70. 55. 62. 94.]
 [71. 79. 90. 91. 68. 80. 55.  0.  0.  0.]]
[[ 1. 13. 12. 11. 69. 42.  7. 43.  5.  0.]
 [78. 74.  8. 27. 86. 31. 36. 46. 82. 32.]
 [49.  9

 [91. 62. 94. 90. 80. 68. 55.  0.  0.  0.]]
[[ 1. 13. 12. 11. 69. 42.  7. 43.  5.  0.]
 [78. 74.  8. 27. 86. 31. 36. 46. 82. 32.]
 [49.  9.  2. 61.  3. 39.  4. 37. 21. 38.]
 [16. 45. 17. 48. 26. 47. 28. 51.  6. 23.]
 [10. 84. 75. 52. 76. 18. 14. 58. 81.  0.]
 [29. 87. 65. 88. 66. 92. 15. 34. 33. 67.]
 [19. 25. 40. 57. 60. 20. 83. 59. 72. 53.]
 [22. 85. 24. 63. 30. 41. 35. 93. 44. 64.]
 [50. 73. 54. 56. 77. 89. 70. 55. 71. 79.]
 [91. 68. 80. 62. 94. 90. 55.  0.  0.  0.]]
[[ 1. 13. 12. 11. 69. 42.  7. 43.  5.  0.]
 [78. 74.  8. 27. 86. 31. 36. 46. 82. 32.]
 [49.  9.  2. 61.  3. 39.  4. 37. 21. 38.]
 [16. 45. 17. 48. 26. 47. 28. 51.  6. 23.]
 [10. 84. 75. 52. 76. 18. 14. 58. 81.  0.]
 [29. 87. 65. 88. 66. 92. 15. 34. 33. 67.]
 [19. 25. 40. 57. 60. 20. 83. 59. 72. 53.]
 [22. 85. 24. 63. 30. 41. 35. 93. 44. 64.]
 [50. 73. 54. 56. 77. 89. 70. 55. 71. 79.]
 [91. 68. 80. 90. 62. 94. 55.  0.  0.  0.]]
[[ 1. 13. 12. 11. 69. 42.  7. 43.  5.  0.]
 [78. 74.  8. 27. 86. 31. 36. 46. 82. 32.]
 [49.  9

 [62. 94. 80. 68. 79. 90. 71.  0.  0.  0.]]
[[ 1. 13. 12. 11. 69. 42.  7. 43.  5.  0.]
 [78. 74.  8. 27. 86. 31. 36. 46. 82. 32.]
 [49.  9.  2. 61.  3. 39.  4. 37. 21. 38.]
 [16. 45. 17. 48. 26. 47. 28. 51.  6. 23.]
 [10. 84. 75. 52. 76. 18. 14. 58. 81.  0.]
 [29. 87. 65. 88. 66. 92. 15. 34. 33. 67.]
 [19. 25. 40. 57. 60. 20. 83. 59. 72. 53.]
 [22. 85. 24. 63. 30. 41. 35. 93. 44. 64.]
 [50. 73. 54. 56. 77. 89. 70. 55. 91. 79.]
 [68. 79. 90. 62. 94. 71. 80.  0.  0.  0.]]
[[ 1. 13. 12. 11. 69. 42.  7. 43.  5.  0.]
 [78. 74.  8. 27. 86. 31. 36. 46. 82. 32.]
 [49.  9.  2. 61.  3. 39.  4. 37. 21. 38.]
 [16. 45. 17. 48. 26. 47. 28. 51.  6. 23.]
 [10. 84. 75. 52. 76. 18. 14. 58. 81.  0.]
 [29. 87. 65. 88. 66. 92. 15. 34. 33. 67.]
 [19. 25. 40. 57. 60. 20. 83. 59. 72. 53.]
 [22. 85. 24. 63. 30. 41. 35. 93. 44. 64.]
 [50. 73. 54. 56. 77. 89. 70. 55. 91. 79.]
 [68. 79. 90. 62. 94. 80. 71.  0.  0.  0.]]
[[ 1. 13. 12. 11. 69. 42.  7. 43.  5.  0.]
 [78. 74.  8. 27. 86. 31. 36. 46. 82. 32.]
 [49.  9

 [91. 80. 68. 79. 90. 55. 71.  0.  0.  0.]]
[[ 1. 13. 12. 11. 69. 42.  7. 43.  5.  0.]
 [78. 74.  8. 27. 86. 31. 36. 46. 82. 32.]
 [49.  9.  2. 61.  3. 39.  4. 37. 21. 38.]
 [16. 45. 17. 48. 26. 47. 28. 51.  6. 23.]
 [10. 84. 75. 52. 76. 18. 14. 58. 81.  0.]
 [29. 87. 65. 88. 66. 92. 15. 34. 33. 67.]
 [19. 25. 40. 57. 60. 20. 83. 59. 72. 53.]
 [22. 85. 24. 63. 30. 41. 35. 93. 44. 64.]
 [50. 73. 54. 56. 77. 89. 70. 62. 94. 62.]
 [91. 80. 68. 79. 90. 71. 55.  0.  0.  0.]]
[[ 1. 13. 12. 11. 69. 42.  7. 43.  5.  0.]
 [78. 74.  8. 27. 86. 31. 36. 46. 82. 32.]
 [49.  9.  2. 61.  3. 39.  4. 37. 21. 38.]
 [16. 45. 17. 48. 26. 47. 28. 51.  6. 23.]
 [10. 84. 75. 52. 76. 18. 14. 58. 81.  0.]
 [29. 87. 65. 88. 66. 92. 15. 34. 33. 67.]
 [19. 25. 40. 57. 60. 20. 83. 59. 72. 53.]
 [22. 85. 24. 63. 30. 41. 35. 93. 44. 64.]
 [50. 73. 54. 56. 77. 89. 70. 62. 94. 62.]
 [91. 90. 79. 68. 80. 71. 55.  0.  0.  0.]]
[[ 1. 13. 12. 11. 69. 42.  7. 43.  5.  0.]
 [78. 74.  8. 27. 86. 31. 36. 46. 82. 32.]
 [49.  9

 [91. 62. 94. 80. 68. 55. 55.  0.  0.  0.]]
[[ 1. 13. 12. 11. 69. 42.  7. 43.  5.  0.]
 [78. 74.  8. 27. 86. 31. 36. 46. 82. 32.]
 [49.  9.  2. 61.  3. 39.  4. 37. 21. 38.]
 [16. 45. 17. 48. 26. 47. 28. 51.  6. 23.]
 [10. 84. 75. 52. 76. 18. 14. 58. 81.  0.]
 [29. 87. 65. 88. 66. 92. 15. 34. 33. 67.]
 [19. 25. 40. 57. 60. 20. 83. 59. 72. 53.]
 [22. 85. 24. 63. 30. 41. 35. 93. 44. 64.]
 [50. 73. 54. 56. 77. 89. 70. 71. 79. 90.]
 [91. 68. 80. 55. 62. 94. 55.  0.  0.  0.]]
[[ 1. 13. 12. 11. 69. 42.  7. 43.  5.  0.]
 [78. 74.  8. 27. 86. 31. 36. 46. 82. 32.]
 [49.  9.  2. 61.  3. 39.  4. 37. 21. 38.]
 [16. 45. 17. 48. 26. 47. 28. 51.  6. 23.]
 [10. 84. 75. 52. 76. 18. 14. 58. 81.  0.]
 [29. 87. 65. 88. 66. 92. 15. 34. 33. 67.]
 [19. 25. 40. 57. 60. 20. 83. 59. 72. 53.]
 [22. 85. 24. 63. 30. 41. 35. 93. 44. 64.]
 [50. 73. 54. 56. 77. 89. 70. 71. 79. 90.]
 [91. 68. 80. 55. 94. 62. 55.  0.  0.  0.]]
[[ 1. 13. 12. 11. 69. 42.  7. 43.  5.  0.]
 [78. 74.  8. 27. 86. 31. 36. 46. 82. 32.]
 [49.  9

In [51]:
obj.VerticleHappiness([5, 6, 8, 10, 46, 60])

Number of People with verticle:


In [47]:
df.loc[11]

First Person     12.0
Second person    69.0
Third person     27.0
Fourth person     NaN
Fifth person      NaN
Name: 11, dtype: float64

In [ ]:
#go through every possible random

In [109]:
matches = []
for person,choices in df.iterrows():
        for rank1,choice in enumerate(choices):
            if person > choice: continue
            if not pd.isnull(choice):
                OtherPersonChoices = list(df.loc[choice])
                if person in OtherPersonChoices:
                    rank2 = OtherPersonChoices.index(person)
                    matches.append({"person1":person,"rank1":rank1+1,"person2":choice, "rank2":rank2+1})
                elif np.isnan(OtherPersonChoices).all():
                    matches.append({"person1":person,"rank1":rank1+1,"person2":choice, "rank2":None})
                
            

In [112]:
    def samePeople(self,pair, p1,p2):
        np1, np2 = pair["person1"],pair["person2"]
        if (np1 == p1 and np2==p2) or (np2 == p1 and np1==p2):
            return True
        return False
    
    
    def removeMatch(self,p1,p2, matches):
        return [pair for pair in matches if not self.samePeople(pair,p1,p2)]
    def verticle(self,row,col):
        verticle = []
        if row!=0:
            verticle.append(self.Chart[row-1][col])
        if row!=10:
            verticle.append(self.Chart[row+1][col])
        return verticle

[[1, 13.0],
 [1, 12.0],
 [3, 61.0],
 [3, 39.0],
 [4, 37.0],
 [4, 21.0],
 [5, 43.0],
 [7, 43.0],
 [7, 42.0],
 [8, 78.0],
 [9, 49.0],
 [10, 84.0],
 [10, 29.0],
 [14, 58.0],
 [15, 34.0],
 [15, 33.0],
 [16, 45.0],
 [18, 52.0],
 [19, 25.0],
 [19, 40.0],
 [20, 83.0],
 [21, 38.0],
 [22, 53.0],
 [22, 57.0],
 [26, 48.0],
 [26, 64.0],
 [27, 86.0],
 [27, 31.0],
 [28, 51.0],
 [29, 87.0],
 [31, 86.0],
 [33, 34.0],
 [36, 82.0],
 [38, 51.0],
 [40, 57.0],
 [42, 69.0],
 [44, 64.0],
 [45, 48.0],
 [50, 73.0],
 [52, 76.0],
 [53, 85.0],
 [54, 56.0],
 [54, 80.0],
 [58, 81.0],
 [59, 83.0],
 [59, 72.0],
 [65, 87.0],
 [65, 84.0],
 [66, 88.0],
 [67, 68.0],
 [68, 79.0],
 [70, 89.0],
 [72, 83.0],
 [75, 84.0],
 [77, 88.0]]

In [97]:
np.isnan([1,2,np.nan]).all()

False

In [82]:
df.loc[13]

First Person      1.0
Second person    78.0
Third person     12.0
Fourth person    34.0
Fifth person     15.0
Name: 13, dtype: float64

In [74]:
matches

[{'person1': 1, 'rank1': 1, 'person2': 13.0, 'rank2': 1},
 {'person1': 1, 'rank1': 2, 'person2': 12.0, 'rank2': 1},
 {'person1': 1, 'rank1': 3, 'person2': 78.0, 'rank2': 2},
 {'person1': 1, 'rank1': 4, 'person2': 8.0, 'rank2': 3},
 {'person1': 1, 'rank1': 5, 'person2': 34.0, 'rank2': 3},
 {'person1': 2, 'rank1': 1, 'person2': 61.0, 'rank2': 3},
 {'person1': 2, 'rank1': 2, 'person2': 42.0, 'rank2': 5},
 {'person1': 2, 'rank1': 3, 'person2': 39.0, 'rank2': 2},
 {'person1': 2, 'rank1': 4, 'person2': 3.0, 'rank2': 3},
 {'person1': 2, 'rank1': 5, 'person2': 69.0, 'rank2': 4},
 {'person1': 3, 'rank1': 1, 'person2': 61.0, 'rank2': 1},
 {'person1': 3, 'rank1': 2, 'person2': 39.0, 'rank2': 1},
 {'person1': 3, 'rank1': 4, 'person2': 69.0, 'rank2': 5},
 {'person1': 4, 'rank1': 1, 'person2': 37.0, 'rank2': 2},
 {'person1': 4, 'rank1': 2, 'person2': 21.0, 'rank2': 2},
 {'person1': 4, 'rank1': 3, 'person2': 14.0, 'rank2': 5},
 {'person1': 4, 'rank1': 4, 'person2': 28.0, 'rank2': 4},
 {'person1': 4, 